In [91]:
import pandas as pd
import numpy as np
import pyarrow as pf
import pyarrow.parquet as pq

In [92]:
# Load the data
file_path = "D:\True Beacon Assignment\data.parquet"
data = pd.read_parquet(file_path)

In [93]:
# Read the parquet dataset into a pyarrow.Table obj
table = pq.read_table(file_path)

In [94]:
# Select the first 6,136 rows of the table
selected_table = table.slice(0, 12272)

In [95]:
# Save the selected table to a new parquet file
pq.write_table(selected_table, 'selected_data.parquet')

In [96]:
#For 30 minutes time frame
chunk_size = 30

In [97]:
# Initialize empty lists
pnl_z_score_spread_list = []
pnl_z_score_iv_ratio_list = []
sharpe_ratio_z_score_iv_ratio_list = []
drawdown_z_score_iv_ratio_list = []

In [98]:
# Loop through data in chunks
for chunk_start in range(0, len(selected_table)-chunk_size):
    
    
    # Get current chunk
    chunk_data = pd.read_parquet(file_path)
    
    # Extract relevant rows using iloc
    chunk_data = chunk_data.iloc[chunk_start:chunk_start + chunk_size]
    
    
        
    ## Calculate the spread and IV ratio for the chunk
    #chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
    #chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
    #chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
    #chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()

    ## Implement trading logic and P/L for each chunk
    chunk_pnl_z_score_spread = []
    chunk_pnl_z_score_iv_ratio = []

    for i in range(len(chunk_data)):
        
        ## Calculate the spread and IV ratio for the chunk
        chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
        chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
        chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
        chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()
        
    
        if chunk_z_score_spread.iloc[i] > 2:
            chunk_pnl_z_score_spread.append((chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_spread.iloc[i] < -2:
            chunk_pnl_z_score_spread.append(-(chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_spread.append(0)

        if chunk_z_score_iv_ratio.iloc[i] > 1:
            chunk_pnl_z_score_iv_ratio.append((chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_iv_ratio.iloc[i] < 1:
            chunk_pnl_z_score_iv_ratio.append(-(chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_iv_ratio.append(0)
            
       
        
    ## Append chunk results to main lists
    pnl_z_score_spread_list.append(np.sum(chunk_pnl_z_score_spread))
    pnl_z_score_iv_ratio_list.append(np.sum(chunk_pnl_z_score_iv_ratio))
    
    if np.std(chunk_pnl_z_score_spread) == 0:
        sharpe_ratio_z_score_spread_list.append(0)
    else:
        sharpe_ratio_z_score_spread_list.append(
        np.mean(chunk_pnl_z_score_spread) / np.std(chunk_pnl_z_score_spread)
        )
    drawdown_z_score_spread_list.append(
        max(np.cumsum(chunk_pnl_z_score_spread) - np.max(np.cumsum(chunk_pnl_z_score_spread)))
    )
    if np.std(chunk_pnl_z_score_iv_ratio) == 0:
        sharpe_ratio_z_score_iv_ratio_list.append(0)
    else:
        sharpe_ratio_z_score_iv_ratio_list.append(
        np.mean(chunk_pnl_z_score_iv_ratio) / np.std(chunk_pnl_z_score_iv_ratio)
        )
    drawdown_z_score_iv_ratio_list.append(
        max(np.cumsum(chunk_pnl_z_score_iv_ratio) - np.max(np.cumsum(chunk_pnl_z_score_iv_ratio)))
    )
    

In [100]:
# Print final results for each chunk
for i in range(len(pnl_z_score_spread_list)):
    print(f"Chunk {i+1}:")
    print(f"    Z-Score Spread P/L: {pnl_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio P/L: {pnl_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread sharp ratio: {sharpe_ratio_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio sharp ratio: {sharpe_ratio_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread drawdown: {drawdown_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio drawdown: {drawdown_z_score_iv_ratio_list[i]}")
    print()

Chunk 1:
    Z-Score Spread P/L: 0
    Z-Score IV Ratio P/L: -187.37855501907492
    Z-Score Spread sharp ratio: nan
    Z-Score IV Ratio sharp ratio: -0.7497219807100549
    Z-Score Spread drawdown: 0
    Z-Score IV Ratio drawdown: 0.0

Chunk 2:
    Z-Score Spread P/L: 0
    Z-Score IV Ratio P/L: -187.3706505318232
    Z-Score Spread sharp ratio: nan
    Z-Score IV Ratio sharp ratio: -0.7497022091615525
    Z-Score Spread drawdown: 0
    Z-Score IV Ratio drawdown: 0.0

Chunk 3:
    Z-Score Spread P/L: 0
    Z-Score IV Ratio P/L: -187.36511297365928
    Z-Score Spread sharp ratio: nan
    Z-Score IV Ratio sharp ratio: -0.749688356277369
    Z-Score Spread drawdown: 0
    Z-Score IV Ratio drawdown: 0.0

Chunk 4:
    Z-Score Spread P/L: 0
    Z-Score IV Ratio P/L: -166.53005031309522
    Z-Score Spread sharp ratio: nan
    Z-Score IV Ratio sharp ratio: -0.6301797676773034
    Z-Score Spread drawdown: 0
    Z-Score IV Ratio drawdown: 0.0

Chunk 5:
    Z-Score Spread P/L: 0
    Z-Score IV 

In [101]:
#For 60 minutes time frame
chunk_size = 60

In [102]:
# Initialize empty lists
pnl_z_score_spread_list = []
pnl_z_score_iv_ratio_list = []


In [ ]:
# Loop through data in chunks
for chunk_start in range(0, len(selected_table)-chunk_size):
    
    
    # Get current chunk
    chunk_data = pd.read_parquet(file_path)
    
    # Extract relevant rows using iloc
    chunk_data = chunk_data.iloc[chunk_start:chunk_start + chunk_size]
    
    
    ## Calculate the spread and IV ratio for the chunk
    #chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
    #chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
    #chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
    #chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()

    ## Implement trading logic and P/L for each chunk
    chunk_pnl_z_score_spread = []
    chunk_pnl_z_score_iv_ratio = []

    for i in range(len(chunk_data)):
        
        ## Calculate the spread and IV ratio for the chunk
        chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
        chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
        chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
        chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()
    
        if chunk_z_score_spread.iloc[i] > 2:
            chunk_pnl_z_score_spread.append((chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_spread.iloc[i] < -2:
            chunk_pnl_z_score_spread.append(-(chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_spread.append(0)

        if chunk_z_score_iv_ratio.iloc[i] > 1:
            chunk_pnl_z_score_iv_ratio.append((chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_iv_ratio.iloc[i] < 1:
            chunk_pnl_z_score_iv_ratio.append(-(chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_iv_ratio.append(0)

    ## Append chunk results to main lists
    pnl_z_score_spread_list.append(np.sum(chunk_pnl_z_score_spread))
    pnl_z_score_iv_ratio_list.append(np.sum(chunk_pnl_z_score_iv_ratio))
    
    if np.std(chunk_pnl_z_score_spread) == 0:
        sharpe_ratio_z_score_spread_list.append(0)
    else:
        sharpe_ratio_z_score_spread_list.append(
        np.mean(chunk_pnl_z_score_spread) / np.std(chunk_pnl_z_score_spread)
        )
    drawdown_z_score_spread_list.append(
        max(np.cumsum(chunk_pnl_z_score_spread) - np.max(np.cumsum(chunk_pnl_z_score_spread)))
    )
    if np.std(chunk_pnl_z_score_iv_ratio) == 0:
        sharpe_ratio_z_score_iv_ratio_list.append(0)
    else:
        sharpe_ratio_z_score_iv_ratio_list.append(
        np.mean(chunk_pnl_z_score_iv_ratio) / np.std(chunk_pnl_z_score_iv_ratio)
        )
    drawdown_z_score_iv_ratio_list.append(
        max(np.cumsum(chunk_pnl_z_score_iv_ratio) - np.max(np.cumsum(chunk_pnl_z_score_iv_ratio)))
    )

In [14]:
# Print final results for each chunk
for i in range(len(pnl_z_score_spread_list)):
    print(f"Chunk {i+1}:")
    print(f"    Z-Score Spread P/L: {pnl_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio P/L: {pnl_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread sharp ratio: {sharpe_ratio_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio sharp ratio: {sharpe_ratio_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread drawdown: {drawdown_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio drawdown: {drawdown_z_score_iv_ratio_list[i]}")
    print()

Chunk 1:
    Z-Score Spread P/L: 70.48713063519241
    Z-Score IV Ratio P/L: 31.315560175677213

Chunk 2:
    Z-Score Spread P/L: 60.42164749416928
    Z-Score IV Ratio P/L: 20.907825639268104

Chunk 3:
    Z-Score Spread P/L: 40.28958907427685
    Z-Score IV Ratio P/L: 10.501200238693066

Chunk 4:
    Z-Score Spread P/L: 30.22255510627282
    Z-Score IV Ratio P/L: 20.91441918894698

Chunk 5:
    Z-Score Spread P/L: 30.221649793565916
    Z-Score IV Ratio P/L: 31.325632734749618

Chunk 6:
    Z-Score Spread P/L: 50.3537240526359
    Z-Score IV Ratio P/L: 20.909664561442927

Chunk 7:
    Z-Score Spread P/L: 40.28656363481721
    Z-Score IV Ratio P/L: 10.495981351144712

Chunk 8:
    Z-Score Spread P/L: 30.219671728528066
    Z-Score IV Ratio P/L: 0.08261426487488421

Chunk 9:
    Z-Score Spread P/L: 20.152399301719846
    Z-Score IV Ratio P/L: 0.08003899907681777

Chunk 10:
    Z-Score Spread P/L: 10.085604965787502
    Z-Score IV Ratio P/L: 0.08003899907681777

Chunk 11:
    Z-Score Sp

In [15]:
#For 1 day time frame
chunk_size = 1440

In [16]:
# Initialize empty lists
pnl_z_score_spread_list = []
pnl_z_score_iv_ratio_list = []


In [17]:
# Loop through data in chunks
for chunk_start in range(0, len(selected_table)-chunk_size):
    
    
    # Get current chunk
    chunk_data = pd.read_parquet(file_path)
    
    # Extract relevant rows using iloc
    chunk_data = chunk_data.iloc[chunk_start:chunk_start + chunk_size]
    
        
    ## Calculate the spread and IV ratio for the chunk
    #chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
    #chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
    #chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
    #chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()

    ## Implement trading logic and P/L for each chunk
    chunk_pnl_z_score_spread = []
    chunk_pnl_z_score_iv_ratio = []

    for i in range(len(chunk_data)):
        
        ## Calculate the spread and IV ratio for the chunk
        chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
        chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
        chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
        chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()
    
        if chunk_z_score_spread.iloc[i] > 2:
            chunk_pnl_z_score_spread.append((chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_spread.iloc[i] < -2:
            chunk_pnl_z_score_spread.append(-(chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_spread.append(0)

        if chunk_z_score_iv_ratio.iloc[i] > 1:
            chunk_pnl_z_score_iv_ratio.append((chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_iv_ratio.iloc[i] < 1:
            chunk_pnl_z_score_iv_ratio.append(-(chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_iv_ratio.append(0)

    ## Append chunk results to main lists
    pnl_z_score_spread_list.append(np.sum(chunk_pnl_z_score_spread))
    pnl_z_score_iv_ratio_list.append(np.sum(chunk_pnl_z_score_iv_ratio))
    
    if np.std(chunk_pnl_z_score_spread) == 0:
        sharpe_ratio_z_score_spread_list.append(0)
    else:
        sharpe_ratio_z_score_spread_list.append(
        np.mean(chunk_pnl_z_score_spread) / np.std(chunk_pnl_z_score_spread)
        )
    drawdown_z_score_spread_list.append(
        max(np.cumsum(chunk_pnl_z_score_spread) - np.max(np.cumsum(chunk_pnl_z_score_spread)))
    )
    if np.std(chunk_pnl_z_score_iv_ratio) == 0:
        sharpe_ratio_z_score_iv_ratio_list.append(0)
    else:
        sharpe_ratio_z_score_iv_ratio_list.append(
        np.mean(chunk_pnl_z_score_iv_ratio) / np.std(chunk_pnl_z_score_iv_ratio)
        )
    drawdown_z_score_iv_ratio_list.append(
        max(np.cumsum(chunk_pnl_z_score_iv_ratio) - np.max(np.cumsum(chunk_pnl_z_score_iv_ratio)))
    )

KeyboardInterrupt: 

In [ ]:
# Print final results for each chunk
for i in range(len(pnl_z_score_spread_list)):
    print(f"Chunk {i+1}:")
    print(f"    Z-Score Spread P/L: {pnl_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio P/L: {pnl_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread sharp ratio: {sharpe_ratio_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio sharp ratio: {sharpe_ratio_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread drawdown: {drawdown_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio drawdown: {drawdown_z_score_iv_ratio_list[i]}")
    print()

In [55]:
#For 5 day time frame
chunk_size = 6136

In [56]:
# Initialize empty lists
pnl_z_score_spread_list = []
pnl_z_score_iv_ratio_list = []

In [ ]:
# Loop through data in chunks
for chunk_start in range(0, len(selected_table)-chunk_size):
    
    
    # Get current chunk
    chunk_data = pd.read_parquet(file_path)
    
    # Extract relevant rows using iloc
    chunk_data = chunk_data.iloc[chunk_start:chunk_start + chunk_size]
        
    ## Calculate the spread and IV ratio for the chunk
    #chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
    #chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
    #chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
    #chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()

    ## Implement trading logic and P/L for each chunk
    chunk_pnl_z_score_spread = []
    chunk_pnl_z_score_iv_ratio = []

    for i in range(len(chunk_data)):
        
        ## Calculate the spread and IV ratio for the chunk
        chunk_spread = chunk_data['banknifty'] - chunk_data['nifty']
        chunk_iv_ratio = chunk_data['banknifty'] / chunk_data['nifty']

    ## Calculate z-scores for the chunk
        chunk_z_score_spread = (chunk_spread - chunk_spread.mean()) / chunk_spread.std()
        chunk_z_score_iv_ratio = (chunk_iv_ratio - chunk_iv_ratio.mean()) / chunk_iv_ratio.std()
    
        if chunk_z_score_spread.iloc[i] > 2:
            chunk_pnl_z_score_spread.append((chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_spread.iloc[i] < -2:
            chunk_pnl_z_score_spread.append(-(chunk_spread.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_spread.append(0)

        if chunk_z_score_iv_ratio.iloc[i] > 1:
            chunk_pnl_z_score_iv_ratio.append((chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        elif chunk_z_score_iv_ratio.iloc[i] < 1:
            chunk_pnl_z_score_iv_ratio.append(-(chunk_iv_ratio.iloc[i] + chunk_data['tte'].iloc[i]) ** 0.7)
        else:
            chunk_pnl_z_score_iv_ratio.append(0)

    ## Append chunk results to main lists
    pnl_z_score_spread_list.append(np.sum(chunk_pnl_z_score_spread))
    pnl_z_score_iv_ratio_list.append(np.sum(chunk_pnl_z_score_iv_ratio))
    
    if np.std(chunk_pnl_z_score_spread) == 0:
        sharpe_ratio_z_score_spread_list.append(0)
    else:
        sharpe_ratio_z_score_spread_list.append(
        np.mean(chunk_pnl_z_score_spread) / np.std(chunk_pnl_z_score_spread)
        )
    drawdown_z_score_spread_list.append(
        max(np.cumsum(chunk_pnl_z_score_spread) - np.max(np.cumsum(chunk_pnl_z_score_spread)))
    )
    if np.std(chunk_pnl_z_score_iv_ratio) == 0:
        sharpe_ratio_z_score_iv_ratio_list.append(0)
    else:
        sharpe_ratio_z_score_iv_ratio_list.append(
        np.mean(chunk_pnl_z_score_iv_ratio) / np.std(chunk_pnl_z_score_iv_ratio)
        )
    drawdown_z_score_iv_ratio_list.append(
        max(np.cumsum(chunk_pnl_z_score_iv_ratio) - np.max(np.cumsum(chunk_pnl_z_score_iv_ratio)))
    )

In [49]:
# Print final results for each chunk
for i in range(len(pnl_z_score_spread_list)):
    print(f"Chunk {i+1}:")
    print(f"    Z-Score Spread P/L: {pnl_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio P/L: {pnl_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread sharp ratio: {sharpe_ratio_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio sharp ratio: {sharpe_ratio_z_score_iv_ratio_list[i]}")
    print(f"    Z-Score Spread drawdown: {drawdown_z_score_spread_list[i]}")
    print(f"    Z-Score IV Ratio drawdown: {drawdown_z_score_iv_ratio_list[i]}")
    print()